In [0]:
dbutils.fs.ls('/mnt/processed')

Out[7]: [FileInfo(path='dbfs:/mnt/processed/circuits/', name='circuits/', size=0, modificationTime=1727451928000),
 FileInfo(path='dbfs:/mnt/processed/constructors/', name='constructors/', size=0, modificationTime=1726340349000),
 FileInfo(path='dbfs:/mnt/processed/drivers/', name='drivers/', size=0, modificationTime=1726395937000),
 FileInfo(path='dbfs:/mnt/processed/lap_times/', name='lap_times/', size=0, modificationTime=1726398426000),
 FileInfo(path='dbfs:/mnt/processed/pitstops/', name='pitstops/', size=0, modificationTime=1726396657000),
 FileInfo(path='dbfs:/mnt/processed/qualifying/', name='qualifying/', size=0, modificationTime=1726397885000),
 FileInfo(path='dbfs:/mnt/processed/races/', name='races/', size=0, modificationTime=1726257403000),
 FileInfo(path='dbfs:/mnt/processed/results/', name='results/', size=0, modificationTime=1726342884000)]

In [0]:
races_df = spark.read.format("parquet").load("/mnt/processed/races")
drivers_df = spark.read.format("parquet").load("/mnt/processed/drivers")
results_df = spark.read.format("parquet").load("/mnt/processed/results")
constructors_df = spark.read.format("parquet").load("/mnt/processed/constructors")
circuits_df = spark.read.format("parquet").load("/mnt/processed/circuits")

In [0]:
races_df = races_df.withColumnRenamed("name", "race_name")\
    .withColumnRenamed("race_timestamp", "race_date")

In [0]:
circuits_df = circuits_df.withColumnRenamed("location", "circuit_location")

In [0]:
drivers_df = drivers_df.withColumnRenamed("name", "driver_name") \
    .withColumnRenamed("nationality", "driver_nationality") \
    .withColumnRenamed("number", "driver_number")

In [0]:
constructors_df = constructors_df.withColumnRenamed("name", "team")

In [0]:
joined_df = circuits_df.join(races_df.alias("race"), ["circuit_id"], "INNER") \
    .join(results_df, ["race_id"], "INNER") \
    .join(drivers_df, ["driver_id"], "INNER") \
    .join(constructors_df, ["constructor_id"], "INNER")


In [0]:
from pyspark.sql.functions import current_timestamp

joined_df = joined_df.select(
    ["race_year", "race_name", "race_date", 
     "circuit_location", 
     "driver_name", "driver_nationality", "driver_number", 
     "team", 
     "grid", "fastest_lap", "position", "points"
    ])
joined_df = joined_df.withColumn("ingestion_time", current_timestamp())

In [0]:
display(joined_df)

race_year race_name race_date circuit_location driver_name driver_nationality driver_number team grid fastest_lap position points ingestion_time 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Sergey Sirotkin Russian 35 Williams 19 3 null 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Marcus Ericsson Swedish 9 Sauber 17 4 null 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Pierre Gasly French 10 Toro Rosso 20 13 null 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Kevin Magnussen Danish 20 Haas F1 Team 5 21 null 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Romain Grosjean French 8 Haas F1 Team 6 23 null 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Brendon Hartley New Zealander 28 Toro Rosso 16 57 15 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Lance Stroll Canadian 18 Williams 13 55 14 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Charles Leclerc Monegasque 16 Sauber 18 56 13 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Esteban Ocon French 31 Force India 14 57 12 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Sergio Pérez Mexican 11 Force India 12 51 11 0.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Carlos Sainz Spanish 55 Renault 9 51 10 1.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Stoffel Vandoorne Belgian 2 McLaren 11 57 9 2.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Valtteri Bottas Finnish 77 Mercedes 15 54 8 4.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Nico Hülkenberg German 27 Renault 7 57 7 6.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Max Verstappen Dutch 33 Red Bull 4 54 6 8.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Fernando Alonso Spanish 14 McLaren 10 57 5 10.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Daniel Ricciardo Australian 3 Red Bull 8 54 4 12.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Kimi Räikkönen Finnish 7 Ferrari 2 57 3 15.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Lewis Hamilton British 44 Mercedes 1 50 2 18.0 2024-09-27T18:33:35.800+0000 2018 Australian Grand Prix 2018-03-25T05:10:00.000+0000 Melbourne Sebastian Vettel German 5 Ferrari 3 53 1 25.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Daniel Ricciardo Australian 3 Red Bull 4 null null 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Max Verstappen Dutch 33 Red Bull 15 null null 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Kimi Räikkönen Finnish 7 Ferrari 2 22 null 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Brendon Hartley New Zealander 28 Toro Rosso 11 42 17 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Sergio Pérez Mexican 11 Force India 12 32 16 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Sergey Sirotkin Russian 35 Williams 18 47 15 0.0 2024-09-27T18:33:35.800+0000 2018 Bahrain Grand Prix 2018-04-08T15:10:00.000+0000 Sakhir Lance Stroll Canadian 18 Williams 20 40 14 0.0 2024-09-27T18:33:35.800+0000 2018 Bahra

In [0]:
display(joined_df.filter("race_year = 2020 and race_name = 'Abu Dhabi Grand Prix'").orderBy("points", ascending=False))

race_year race_name race_date circuit_location driver_name driver_nationality driver_number team grid fastest_lap position points ingestion_time 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Max Verstappen Dutch 33 Red Bull 1 14 1 25.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Valtteri Bottas Finnish 77 Mercedes 2 40 2 18.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Lewis Hamilton British 44 Mercedes 3 37 3 15.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Alexander Albon Thai 23 Red Bull 5 42 4 12.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Lando Norris British 4 McLaren 4 53 5 10.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Carlos Sainz Spanish 55 McLaren 6 48 6 8.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Daniel Ricciardo Australian 3 Renault 11 55 7 7.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Pierre Gasly French 10 AlphaTauri 9 53 8 4.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Esteban Ocon French 31 Renault 10 47 9 2.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Lance Stroll Canadian 18 Racing Point 8 41 10 1.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Sergio Pérez Mexican 11 Racing Point 19 6 null 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Pietro Fittipaldi Brazilian 51 Haas F1 Team 17 50 19 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Kevin Magnussen Danish 20 Haas F1 Team 20 50 18 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Nicholas Latifi Canadian 6 Williams 18 49 17 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Antonio Giovinazzi Italian 99 Alfa Romeo 14 29 16 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi George Russell British 63 Williams 16 54 15 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Sebastian Vettel German 5 Ferrari 13 37 14 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Charles Leclerc Monegasque 16 Ferrari 12 24 13 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Kimi Räikkönen Finnish 7 Alfa Romeo 15 53 12 0.0 2024-09-27T18:37:52.068+0000 2020 Abu Dhabi Grand Prix 2020-12-13T13:10:00.000+0000 Abu Dhabi Daniil Kvyat Russian 26 AlphaTauri 7 47 11 0.0 2024-09-27T18:37:52.068+0000

In [0]:
joined_df.write.mode("overwrite").parquet("/mnt/presentation/race_results")